In [4]:
import os
import json

import numpy as np
import pandas as pd
from pandas.io.json import json_normalize

In [5]:
train = pd.read_csv('data/train.csv')
train.tail(3)

date                            nextDayPlayerEngagement  \
1213  20210428  [{"engagementMetricsDate":"2021-04-29","player...   
1214  20210429  [{"engagementMetricsDate":"2021-04-30","player...   
1215  20210430  [{"engagementMetricsDate":"2021-05-01","player...   

                                                  games  \
1213  [{"gamePk":634309,"gameType":"R","season":2021...   
1214  [{"gamePk":634330,"gameType":"R","season":2021...   
1215  [{"gamePk":634287,"gameType":"R","season":2021...   

                                                rosters  \
1213  [{"playerId":429722,"gameDate":"2021-04-28","t...   
1214  [{"playerId":405395,"gameDate":"2021-04-29","t...   
1215  [{"playerId":405395,"gameDate":"2021-04-30","t...   

                                        playerBoxScores  \
1213  [{"home":1,"gamePk":634310,"gameDate":"2021-04...   
1214  [{"home":1,"gamePk":634330,"gameDate":"2021-04...   
1215  [{"home":1,"gamePk":634305,"gameDate":"2021-04...   

                                          teamBoxScores  \
1213  [{"home":0,"teamId":111,"gamePk":634310,"gameD...   
1214  [{"home":0,"teamId":119,"gamePk":634346,"gameD...   
1215  [{"home":1,"teamId":135,"gamePk":634303,"gameD...   

                                           transactions  \
1213  [{"transactionId":480728,"playerId":545358,"pl...   
1214  [{"transactionId":480993,"playerId":606965,"pl...   
1215                                                NaN   

                                              standings  \
1213  [{"season":2021,"gameDate":"2021-04-28","divis...   
1214  [{"season":2021,"gameDate":"2021-04-29","divis...   
1215  [{"season":2021,"gameDate":"2021-04-30","divis...   

                                                 awards  \
1213                                                NaN   
1214                                                NaN   
1215  [{"awardId":"NLRRELMON","awardName":"NL Reliev...   

                                                 events  \
1213  [{"gamePk":634317,"gameDate":"2021-04-28","gam...   
1214  [{"gamePk":634346,"gameDate":"2021-04-29","gam...   
1215  [{"gamePk":634327,"gameDate":"2021-04-30","gam...   

     playerTwitterFollowers teamTwitterFollowers  
1213                    NaN                  NaN  
1214                    NaN                  NaN  
1215                    NaN                  NaN

In [7]:
train.columns

Index(['date', 'nextDayPlayerEngagement', 'games', 'rosters',
       'playerBoxScores', 'teamBoxScores', 'transactions', 'standings',
       'awards', 'events', 'playerTwitterFollowers', 'teamTwitterFollowers'],
      dtype='object')

In [9]:
train['events'].iloc[88]

'[{"gamePk":529422,"gameDate":"2018-03-30","gameTimeUTC":"2018-03-30T23:10:00Z","season":2018,"gameType":"R","playId":null,"eventId":1,"inning":5,"halfInning":"bottom","homeScore":1,"awayScore":1,"menOnBase":null,"atBatIndex":40,"atBatDesc":"Marlins challenged (play at 1st), call on the field was overturned: Derek Dietrich grounds into a force out, third baseman Kris Bryant to shortstop Addison Russell.   Lewis Brinson out at 2nd.    Derek Dietrich to 1st.","atBatEvent":"Forceout","hasOut":1,"pitcherTeamId":112,"isPitcherHome":0,"pitcherTeam":"Chicago Cubs","hitterTeamId":146,"hitterTeam":"Miami Marlins","pitcherId":543294,"pitcherName":"Kyle Hendricks","isStarter":1,"pitcherHand":"R","hitterId":518618,"hitterName":"Derek Dietrich","batSide":"L","pitchNumber":2,"balls":0,"strikes":1,"isGB":null,"isLD":null,"isFB":null,"isPU":null,"launchSpeed":null,"launchAngle":null,"totalDistance":null,"event":"Injury","description":"Miami Marlins  Garrett Cooper left the game due to an injured wrist

In [42]:
    for i in range(train.shape[0]):
        print(i)
        cell = train.iloc[i]['events']
        if cell is not None:
            # If a cell is not None make list
            try:
                value = ast.literal_eval(cell)
            except ValueError:
                continue
            for k, v in enumerate(value):
                print(v)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [3]:
example_sub = pd.read_csv('data/example_sample_submission.csv')
example_sub.head()

date    date_playerId  target1  target2  target3  target4
0  20210426  20210427_656669        0        0        0        0
1  20210426  20210427_543475        0        0        0        0
2  20210426  20210427_592866        0        0        0        0
3  20210426  20210427_452678        0        0        0        0
4  20210426  20210427_570257        0        0        0        0

In [4]:
example_test = pd.read_csv('data/example_test.csv')
example_test.head()

date                                              games  \
0  20210426  [{"gamePk":634374,"gameType":"R","season":2021...   
1  20210427  [{"gamePk":634318,"gameType":"R","season":2021...   
2  20210428  [{"gamePk":634309,"gameType":"R","season":2021...   
3  20210429  [{"gamePk":634330,"gameType":"R","season":2021...   
4  20210430  [{"gamePk":634287,"gameType":"R","season":2021...   

                                             rosters  \
0  [{"playerId":405395,"gameDate":"2021-04-26","t...   
1  [{"playerId":443558,"gameDate":"2021-04-27","t...   
2  [{"playerId":429722,"gameDate":"2021-04-28","t...   
3  [{"playerId":405395,"gameDate":"2021-04-29","t...   
4  [{"playerId":405395,"gameDate":"2021-04-30","t...   

                                     playerBoxScores  \
0  [{"home":1,"gamePk":634377,"gameDate":"2021-04...   
1  [{"home":1,"gamePk":634320,"gameDate":"2021-04...   
2  [{"home":1,"gamePk":634310,"gameDate":"2021-04...   
3  [{"home":1,"gamePk":634330,"gameDate":"2021-04...   
4  [{"home":1,"gamePk":634305,"gameDate":"2021-04...   

                                       teamBoxScores  \
0  [{"home":1,"teamId":139,"gamePk":634343,"gameD...   
1  [{"home":1,"teamId":117,"gamePk":634333,"gameD...   
2  [{"home":0,"teamId":111,"gamePk":634310,"gameD...   
3  [{"home":0,"teamId":119,"gamePk":634346,"gameD...   
4  [{"home":1,"teamId":135,"gamePk":634303,"gameD...   

                                        transactions  \
0  [{"transactionId":480386,"playerId":543685,"pl...   
1  [{"transactionId":480456,"playerId":642162,"pl...   
2  [{"transactionId":480728,"playerId":545358,"pl...   
3  [{"transactionId":480993,"playerId":606965,"pl...   
4                                                NaN   

                                           standings  \
0  [{"season":2021,"gameDate":"2021-04-26","divis...   
1  [{"season":2021,"gameDate":"2021-04-27","divis...   
2  [{"season":2021,"gameDate":"2021-04-28","divis...   
3  [{"season":2021,"gameDate":"2021-04-29","divis...   
4  [{"season":2021,"gameDate":"2021-04-30","divis...   

                                              awards  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4  [{"awardId":"NLRRELMON","awardName":"NL Reliev...   

                                              events  playerTwitterFollowers  \
0  [{"gamePk":634433,"gameDate":"2021-04-26","gam...                     NaN   
1  [{"gamePk":634332,"gameDate":"2021-04-27","gam...                     NaN   
2  [{"gamePk":634317,"gameDate":"2021-04-28","gam...                     NaN   
3  [{"gamePk":634346,"gameDate":"2021-04-29","gam...                     NaN   
4  [{"gamePk":634327,"gameDate":"2021-04-30","gam...                     NaN   

   teamTwitterFollowers  
0                   NaN  
1                   NaN  
2                   NaN  
3                   NaN  
4                   NaN

In [11]:
# 5 rows only
seasons = pd.read_csv('data/seasons.csv')
seasons

seasonId seasonStartDate seasonEndDate preSeasonStartDate preSeasonEndDate  \
0      2017      2017-04-02    2017-11-01         2017-02-22       2017-04-01   
1      2018      2018-03-29    2018-10-28         2018-02-21       2018-03-27   
2      2019      2019-03-20    2019-10-30         2019-02-21       2019-03-26   
3      2020      2020-07-23    2020-10-28         2020-02-21       2020-07-22   
4      2021      2021-02-28    2021-10-31         2021-02-28       2021-03-30   

  regularSeasonStartDate regularSeasonEndDate lastDate1stHalf allStarDate  \
0             2017-04-02           2017-10-01      2017-07-09  2017-07-11   
1             2018-03-29           2018-10-01      2018-07-15  2018-07-17   
2             2019-03-20           2019-09-29      2019-07-07  2019-07-09   
3             2020-07-23           2020-09-27      2020-08-25         NaN   
4             2021-04-01           2021-10-03      2021-07-11  2021-07-13   

  firstDate2ndHalf postSeasonStartDate postSeasonEndDate  
0       2017-07-14          2017-10-03        2017-11-01  
1       2018-07-19          2018-10-02        2018-10-28  
2       2019-07-11          2019-10-01        2019-10-30  
3       2020-08-26          2020-09-29        2020-10-28  
4       2021-07-15          2021-10-04        2021-10-31

In [13]:
# 30 rows and 13 columns
teams = pd.read_csv('data/teams.csv')
teams.head()

id                  name teamName teamCode  shortName abbreviation  \
0  108    Los Angeles Angels   Angels      ana  LA Angels          LAA   
1  109  Arizona Diamondbacks  D-backs      ari    Arizona          ARI   
2  110     Baltimore Orioles  Orioles      bal  Baltimore          BAL   
3  111        Boston Red Sox  Red Sox      bos     Boston          BOS   
4  112          Chicago Cubs     Cubs      chn   Chi Cubs          CHC   

  locationName  leagueId       leagueName  divisionId  \
0      Anaheim       103  American League         200   
1      Phoenix       104  National League         203   
2    Baltimore       103  American League         201   
3       Boston       103  American League         201   
4      Chicago       104  National League         205   

              divisionName  venueId                    venueName  
0     American League West        1                Angel Stadium  
1     National League West       15                  Chase Field  
2     American League East        2  Oriole Park at Camden Yards  
3     American League East        3                  Fenway Park  
4  National League Central       17                Wrigley Field

In [15]:
# 11245 rows
awards = pd.read_csv('data/awards.csv')
awards.head()

awardDate  awardSeason      awardId                       awardName  \
0  2017-12-21         2017  WARRENSPAHN              Warren Spahn Award   
1  2017-12-20         2017    MILBORGAS  MiLB.com Organization All-Star   
2  2017-12-20         2017    MILBORGAS  MiLB.com Organization All-Star   
3  2017-12-20         2017    MILBORGAS  MiLB.com Organization All-Star   
4  2017-12-20         2017    MILBORGAS  MiLB.com Organization All-Star   

   playerId       playerName  awardPlayerTeamId  
0    477132  Clayton Kershaw              119.0  
1    474319   Brandon Snyder              120.0  
2    592530  Jose Marmolejos              120.0  
3    593833     Wander Suero              120.0  
4    600466       Raudy Read              120.0

In [19]:
train.games

0                                                     NaN
1                                                     NaN
2                                                     NaN
3                                                     NaN
4                                                     NaN
                              ...                        
1211    [{"gamePk":634374,"gameType":"R","season":2021...
1212    [{"gamePk":634318,"gameType":"R","season":2021...
1213    [{"gamePk":634309,"gameType":"R","season":2021...
1214    [{"gamePk":634330,"gameType":"R","season":2021...
1215    [{"gamePk":634287,"gameType":"R","season":2021...
Name: games, Length: 1216, dtype: object